In [8]:
from joblib import load

from dask.distributed import Client
import odc.geo.xr
import pandas as pd
from dea_tools.spatial import subpixel_contours

from dep_coastlines.clean_rasters import Cleaner, calculate_consensus_land, remove_disconnected_land
from dep_coastlines.MosaicLoader import MultiyearMosaicLoader

In [2]:
cleaner = Cleaner()

In [3]:
loader = MultiyearMosaicLoader(start_year=2017, end_year=2022)

cell = (48, 14)
df = pd.DataFrame([cell])
df.index = [cell]
ds = loader.load(df)
ds

<xarray.Dataset>
Dimensions:          (x: 3079, y: 3080, year: 6)
Coordinates:
    band             int64 1
  * x                (x) float64 6.202e+05 6.202e+05 ... 7.125e+05 7.125e+05
  * y                (y) float64 -2.438e+06 -2.438e+06 ... -2.53e+06 -2.53e+06
    spatial_ref      int64 0
  * year             (year) <U4 '2017' '2018' '2019' '2020' '2021' '2022'
Data variables: (12/57)
    blue             (year, y, x) float32 dask.array<chunksize=(1, 3080, 3079), meta=np.ndarray>
    blue_mad         (year, y, x) float32 dask.array<chunksize=(1, 3080, 3079), meta=np.ndarray>
    count            (year, y, x) float32 dask.array<chunksize=(1, 3080, 3079), meta=np.ndarray>
    green            (year, y, x) float32 dask.array<chunksize=(1, 3080, 3079), meta=np.ndarray>
    green_mad        (year, y, x) float32 dask.array<chunksize=(1, 3080, 3079), meta=np.ndarray>
    nir08            (year, y, x) float32 dask.array<chunksize=(1, 3080, 3079), meta=np.ndarray>
    ...               ...
    swir22_mad_all   (y, x) float32 dask.array<chunksize=(3080, 3079), meta=np.ndarray>
    mndwi_all        (y, x) float32 dask.array<chunksize=(3080, 3079), meta=np.ndarray>
    ndwi_all         (y, x) float32 dask.array<chunksize=(3080, 3079), meta=np.ndarray>
    nirwi_all        (y, x) float32 dask.array<chunksize=(3080, 3079), meta=np.ndarray>
    meanwi_all       (y, x) float32 dask.array<chunksize=(3080, 3079), meta=np.ndarray>
    maxwi_all        (y, x) float32 dask.array<chunksize=(3080, 3079), meta=np.ndarray>

In [21]:
with Client():
    output = cleaner.model.apply_mask(ds)

predicting...
predicting...
predicting...
predicting...
predicting...
predicting...


In [5]:
import folium

m= output.sel(year='2022').nir08.odc.explore(layer_control=False)
m = ds.sel(year='2022').nir08.odc.explore(map=m)
#folium.LayerControl().add_to(m) 

m



/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(


In [5]:
candidate_land = cleaner.land(output)
candidate_land.sel(year='2022').odc.explore()

/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(


In [6]:
consensus_land = calculate_consensus_land(ds.isel(year=0)).compute()
consensus_land.odc.explore()

In [9]:
connected_areas = remove_disconnected_land(consensus_land, candidate_land.compute())
connected_areas.sel(year='2022').astype(int).odc.explore()

In [14]:
import xrspatial as xs
no_connected_neighbors = xs.focal.mean(consensus_land) == 0
suspicious_connected_areas = candidate_land & no_connected_neighbors
analysis_zone = connected_areas & ~suspicious_connected_areas
analysis_zone.sel(year='2022').astype(int).odc.explore()

In [15]:
analysis_zone = cleaner.expand_analysis_zone(analysis_zone, output)
analysis_zone.sel(year='2022').astype(int).odc.explore()

In [16]:
from odc.algo import mask_cleanup
from dep_coastlines.raster_cleaning import load_gadm_land, find_inland_areas


gadm_land = load_gadm_land(output)
gadm_ocean = mask_cleanup(~gadm_land, mask_filters=[("erosion", 2)])
consensus_ocean = mask_cleanup(~consensus_land, mask_filters=[("erosion", 2)])
consensus_ocean.astype(int).rio.to_raster('../conn_ocean_48_14.tif')

land = gadm_land | consensus_land
ocean = mask_cleanup(~land, mask_filters=[("erosion", 2)])
# ocean.astype(int).rio.to_raster('../2ocean_48_14.tif')


In [17]:
inland_areas = find_inland_areas(cleaner.water(output), ocean)
inland_areas.sel(year='2022').astype(int).odc.explore()

In [34]:
analysis_zone = analysis_zone | mask_cleanup(cleaner.land(output.where(analysis_zone)), mask_filters=[("dilation", 1)])
# output.ndwi.where(analysis_zone).sel(year='2022').odc.explore()

output.ndwi.where(analysis_zone, 0.5).rio.to_raster('../o5.tif')

In [35]:
combined_gdf = subpixel_contours(
    output.ndwi.where(analysis_zone, 0.5),
    dim="year",
    z_values=[cleaner.index_threshold],
    min_vertices=5,
)
combined_gdf.explore()

combined_gdf.to_file('c5.gpkg')

Loading data into memory using Dask
Operating in single z-value, multiple arrays mode


In [18]:
output = output['ndwi'].where(analysis_zone, 0.5).compute()
output.sel(year='2022').odc.explore()

In [20]:

#output = (
#    output[cleaner.water_index]
#    .where(analysis_zone, obvious_water)
#    .where(~inland_areas)
#)
#output = output.groupby("year").map(xs.focal.mean)
combined_gdf = subpixel_contours(
    output,
    dim="year",
    z_values=[cleaner.index_threshold],
    min_vertices=5,
)
combined_gdf.explore()

Operating in single z-value, multiple arrays mode
